In [28]:
import numpy as np

import grpc

import tensorflow as tf

from tensorflow_serving.apis import predict_pb2
from tensorflow_serving.apis import prediction_service_pb2_grpc

from keras_image_helper import create_preprocessor

In [3]:
host = "localhost:8500"

channel = grpc.insecure_channel(host)

stub = prediction_service_pb2_grpc.PredictionServiceStub(channel)

In [4]:
stub

In [6]:
preprocessor = create_preprocessor('xception', target_size=(299, 299))

In [7]:
url = "https://datasets-server.huggingface.co/assets/beans/--/default/test/9/image/image.jpg"
X = preprocessor.from_url(url)

In [12]:
X.shape

(1, 299, 299, 3)

In [13]:
def np_to_protobuf(data):
    return tf.make_tensor_proto(data, shape=data.shape)

In [15]:
pb_request = predict_pb2.PredictRequest()
pb_request.model_spec.name = "beans-model"
pb_request.model_spec.signature_name = "serving_default"

pb_request.inputs['input_26'].CopyFrom(np_to_protobuf(X))

In [16]:
pb_request

model_spec {
  name: "beans-model"
  signature_name: "serving_default"
}
inputs {
  key: "input_26"
  value {
    dtype: DT_FLOAT
    tensor_shape {
      dim {
        size: 1
      }
      dim {
        size: 299
      }
      dim {
        size: 299
      }
      dim {
        size: 3
      }
    }
    tensor_content: "\230\226\226>\240\234\034>\000\361p=\260\2600\275\274\274<\276\216\216\216\276\246\246\246\276\356\356\356\276\220\217\017\277\360\360p\275\314\314L\276\226\226\226\276\206\205\005\277\252\251)\277\302\301A\277\356\356\356\276\234\233\033\277\264\2633\277\246\246\246\276\356\356\356\276\220\217\017\277\216\216\216\276\326\326\326\276\204\203\003\277\230\230\230\275\334\334\\\276\236\236\236\276\300\300@\274\234\234\034\276\374\374|\276\204\204\004\276\212\212\212\276\302\302\302\276\000\301@<\204\204\004\276\364\364t\276\300\300@\274\234\234\034\276\206\206\206\276\340\320P=\270\270\270\275\314\314L\276\000\301@<\204\204\004\276\364\364t\276\220\210\210=\230\230\230\2

In [18]:
pb_response = stub.Predict(pb_request, timeout=20.0)

In [19]:
pb_response

outputs {
  key: "dense_19"
  value {
    dtype: DT_FLOAT
    tensor_shape {
      dim {
        size: 1
      }
      dim {
        size: 3
      }
    }
    float_val: -4.811046600341797
    float_val: -3.5068438053131104
    float_val: -7.72806453704834
  }
}
model_spec {
  name: "beans-model"
  version {
    value: 1
  }
  signature_name: "serving_default"
}

In [24]:
preds = pb_response.outputs['dense_19'].float_val

In [25]:
classes = [
    "angular_leaf_spot",
    "bean_rust",
    "healthy"
]

In [26]:
dict(zip(classes, preds))

{'angular_leaf_spot': -4.811046600341797,
 'bean_rust': -3.5068438053131104,
 'healthy': -7.72806453704834}

In [29]:
min(dict(zip(classes, np.abs(preds))))

'angular_leaf_spot'

In [30]:
!jupyter nbconvert --to script tf-serving.ipynb

[NbConvertApp] Converting notebook tf-serving.ipynb to script
[NbConvertApp] Writing 1387 bytes to tf-serving.py
